In [1]:
%load_ext autoreload
%autoreload 2

In [3]:
%%time
!python --version
!pip show transformers torch torchvision torchaudio

Python 3.11.9
Name: transformers
Version: 4.41.2
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /Users/inflaton/anaconda3/envs/logical-reasoning/lib/python3.11/site-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenizers, tqdm
Required-by: peft
---
Name: torch
Version: 2.5.0.dev20240720
Summary: Tensors and Dynamic neural networks in Python with strong GPU acceleration
Home-page: https://pytorch.org/
Author: PyTorch Team
Author-email: packages@pytorch.org
License: BSD-3
Location: /Users/inflaton/anaconda3/envs/logical-reasoning/lib/python3.11/site-packages
Requires: filelock, fsspec, jinja2, networkx, sympy, typing-exten

In [4]:
from pathlib import Path

try:
    from google.colab import drive

    drive.mount("/content/drive")
    workding_dir = "/content/drive/MyDrive/logical-reasoning/"
except ModuleNotFoundError:
    workding_dir = str(Path.cwd().parent)

In [5]:
import os
import sys
from pathlib import Path

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /Users/inflaton/code/engd/projects/logical-reasoning


In [6]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /Users/inflaton/code/engd/projects/logical-reasoning/.env


True

In [7]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

internlm/internlm2_5-7b-chat-1m llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175 False datasets/mgtv results/mgtv-results_m3.csv


In [8]:
from llm_toolkit.llm_utils import *
from llm_toolkit.logical_reasoning_utils import *

device = check_gpu()

loading /Users/inflaton/code/engd/projects/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
MPS is available


In [9]:
%%time

model, tokenizer = load_model(model_name, dtype=torch.bfloat16, adapter_name_or_path=adapter_name_or_path, using_llama_factory=False)
model.dtype, model.get_memory_footprint()

loading model: internlm/internlm2_5-7b-chat-1m with adapter: llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

CPU times: user 3.33 s, sys: 2.24 s, total: 5.57 s
Wall time: 7.48 s


(torch.bfloat16, 15513174016)

In [10]:
datasets = load_logical_reasoning_dataset(
    data_path,
    tokenizer=tokenizer,
    chinese_prompt=not use_english_datasets,
    using_p1=False,
)

loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 25000
    })
    test: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 3000
    })
})


In [11]:
print_row_details(datasets["test"].to_pandas(), [1000])

--------------------------------------------------
text: 哭泣和村庄有关系吗
--------------------------------------------------
label: 是
--------------------------------------------------
answer: nan
--------------------------------------------------
title: 甄庄哭声
--------------------------------------------------
puzzle: 在一个安静的夜晚，小村庄的湖边突然传来了阵阵哭泣声。第二天早晨，村长甄锐发现湖边的石头上放着一顶破旧的帽子，但没有人知道这顶帽子是从哪里来的，哭泣声又是为何。请还原故事真相。
--------------------------------------------------
truth: 原来，这顶破旧的帽子属于一个小男孩，他小时候与爷爷在湖边生活。爷爷教他钓鱼、游泳，还告诉他湖中的海龟是他们的朋友。后来，小男孩随父母去了城市生活，但每年夏天都会回到村子探望爷爷。然而，去年夏天，爷爷因病去世，小男孩伤心欲绝。今年夏天，他回到村子，来到湖边，想起和爷爷的美好回忆，忍不住哭泣。他将爷爷的帽子放在湖边的石头上，希望能让爷爷的在天之灵得到安慰。那晚的哭泣声正是小男孩在祭莫他亲爱的爷爷。
--------------------------------------------------
train_text: <s><|im_start|>system
You are an expert in logical reasoning.<|im_end|>
<|im_start|>user
你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是

In [12]:
%%time

prompt1 = datasets["test"]["prompt"][1000]

gen_kwargs = {"max_length": 4096, "do_sample": True, "top_k": 1}
with torch.no_grad():
    inputs = tokenizer(
        [prompt1],
        return_tensors="pt",
    ).to(device)
    outputs = model.generate(**inputs, **gen_kwargs)
    outputs = outputs[:, inputs['input_ids'].shape[1]:]
    print(tokenizer.decode(outputs[0], skip_special_tokens=True))

是
CPU times: user 619 ms, sys: 392 ms, total: 1.01 s
Wall time: 1.9 s


In [13]:
def evaluate_model(model, tokenizer, dataset, batch_size=8):
    save_model_name = f"{model_name}_{adapter_name_or_path}_m3_{model.dtype}"
    print(f"Evaluating model: {save_model_name} on {device}")
    predictions = eval_model(
        model, tokenizer, dataset, device=device, batch_size=batch_size
    )

    save_results(
        save_model_name,
        results_path,
        dataset,
        predictions,
        debug=False,
    )

    metrics = calc_metrics(dataset["label"], predictions, debug=False)
    print(metrics)

In [14]:
%%time

evaluate_model(model, tokenizer, datasets["test"])

Evaluating model: internlm/internlm2_5-7b-chat-1m_llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175_m3_torch.bfloat16 on mps


  0%|          | 1/375 [00:15<1:35:45, 15.36s/it]

Batch output: ['不是', '是', '是', '是', '不是', '是', '是', '不是']


100%|██████████| 375/375 [2:42:25<00:00, 25.99s/it]   


{'accuracy': 0.807}
CPU times: user 5min 2s, sys: 5min 33s, total: 10min 35s
Wall time: 2h 42min 25s


In [15]:
%%time

del model, tokenizer

model, tokenizer = load_model(model_name, dtype=torch.float16, adapter_name_or_path=adapter_name_or_path, using_llama_factory=False)
model.dtype, model.get_memory_footprint()

loading model: internlm/internlm2_5-7b-chat-1m with adapter: llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

CPU times: user 23.1 s, sys: 10.9 s, total: 34 s
Wall time: 16.1 s


(torch.float16, 15513174016)

In [16]:
%%time

evaluate_model(model, tokenizer, datasets["test"])

Evaluating model: internlm/internlm2_5-7b-chat-1m_llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175_m3_torch.float16 on mps


  0%|          | 1/375 [00:19<1:59:08, 19.11s/it]

Batch output: ['不是', '是', '是', '是', '不是', '是', '是', '不是']


100%|██████████| 375/375 [2:19:06<00:00, 22.26s/it]  

{'accuracy': 0.8023333333333333}
CPU times: user 3min 14s, sys: 4min 37s, total: 7min 52s
Wall time: 2h 19min 6s


In [21]:
%%time

del model, tokenizer

model, tokenizer = load_model(model_name, dtype=torch.float32, adapter_name_or_path=adapter_name_or_path, using_llama_factory=False)
model.dtype, model.get_memory_footprint()

loading model: internlm/internlm2_5-7b-chat-1m with adapter: llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

CPU times: user 34.8 s, sys: 13 s, total: 47.8 s
Wall time: 10.5 s


(torch.float32, 31026339840)

In [22]:
%%time

evaluate_model(model, tokenizer, datasets["test"])

Evaluating model: internlm/internlm2_5-7b-chat-1m_llama-factory/saves/internlm2_5_7b/lora/sft_bf16_p2_full_r2/checkpoint-175_m3_torch.float32 on mps


  0%|          | 1/375 [00:20<2:07:18, 20.42s/it]

Batch output: ['不是', '是', '是', '是', '不是', '是', '是', '不是']


100%|██████████| 375/375 [5:23:51<00:00, 51.82s/it]    


{'accuracy': 0.8016666666666666}
CPU times: user 4min 1s, sys: 10min 4s, total: 14min 6s
Wall time: 5h 23min 51s
